# **LongMemory.jl**: Generating, Estimating, and Forecasting Long Memory

Models in ***Julia***

Benchmarks

[J. Eduardo Vera-Valdés,
<eduardo@math.aau.dk>](mailto:eduardo@math.aau.dk)

# Abstract

**LongMemory.jl** is a package for time series long memory modelling in
***Julia***. The package provides functions for generating long memory,
estimating the parameters of the models, and simulation. Generating
methods include fractional differencing, stochastic error duration, and
cross-sectional aggregation. Estimators include those inspired by the
log-periodogram regression and parametric ones. This notebook provides
benchmarks for the **LongMemory.jl** package including against current
alternatives. The package is closely related to the ***R*** packages
**LongMemoryTS** and **fracdiff**.

# Citation

If you use this package in your research, please cite it as:

### Text

Vera-Valdés, J.E. (2024). “LongMemory.jl: Generating, Estimating, and
Forecasting Long Memory Models in Julia”. arXiv 2401.14077.
<https://arxiv.org/abs/2401.14077>

### BibTex

``` bibtex
@article{VERAVALDES2024a,
title = {LongMemory.jl: Generating, Estimating, and Forecasting Long Memory Models in Julia},
year = {2024},
author = {Vera-Valdés, J.E.},
journal = {arXiv preprint arXiv:2401.14077},
url = {https://arxiv.org/abs/2401.14077}
}
```

# Loading packages

Loading the package and setting a seed

In [2]:
using LongMemory, BenchmarkTools, Random, RCall
Random.seed!(1234)

TaskLocalRNG()

# Long memory generation

## The *fi_gen()* function, which uses the cumulative method.

In [3]:
@benchmark fi_gen(10000, 0.2)

BenchmarkTools.Trial: 4197 samples with 1 evaluation.
 Range ( min … max ): 612.500 μs … 9.615 ms ┊ GC ( min … max ): 0.00% … 52.21%
 Time ( median ): 818.100 μs ┊ GC ( median ): 0.00%
 Time ( mean ± σ ): 1.166 ms ± 885.597 μs ┊ GC ( mean ± σ ): 6.15% ± 6.76%
 ██▆ ▅ ▅▄▄▄ ▄ ▄▄▄▄▃▂▂▂▁▁ ▂
 ███ █ ████ █ ██████████████▇▆▇▆▆▅▆▃▁▅▁▃▁▅▄▆▆▇▇████▆█▇▇▇▆▅▃▆▆▅▆▅▅▇ █
 612 μs Histogram: log( frequency ) by time 4.76 ms < 
 Memory estimate : 2.58 MiB , allocs estimate : 44 .

## R: benchmarking the *fracdiff.sim()* function.

Loading the ***R*** packages. The ***R*** package **fracdiff** is used
for fractional differencing generation using
***fracdiff::fracdiff.sim()***. Benchmarking the fractional differencing
generation by the ***R*** package **fracdiff** using **RCall**.

In [4]:
R"library(fracdiff)"
@benchmark R"fracdiff::fracdiff.sim(10000, d = 0.2)"

┌ Warning: RCall.jl: Warning: package 'fracdiff' was built under R version 4.3.3
└ @ RCall C:\Users\eduar\.julia\packages\RCall\FEbLj\src\io.jl:172

BenchmarkTools.Trial: 45 samples with 1 evaluation.
 Range ( min … max ): 103.105 ms … 143.818 ms ┊ GC ( min … max ): 0.00% … 0.00%
 Time ( median ): 112.318 ms ┊ GC ( median ): 0.00%
 Time ( mean ± σ ): 112.891 ms ± 8.028 ms ┊ GC ( mean ± σ ): 0.00% ± 0.00%
 █ ▄▁▁▁ ▄ ▄ ▁▄▁ ▁ 
 █▆████▆▆█▆▁▆▆ ▆ █ ▆ ▆▁▆▆▁███▁▆▆▁▆█▆▆▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▆ ▁
 103 ms Histogram: frequency by time 144 ms < 
 Memory estimate : 1.02 KiB , allocs estimate : 37 .

### For comparison purposes, the following benchmark is done in ***R*** using the **microbenchmark** package.

In [5]:
R"library(microbenchmark)"
R"microbenchmark(fracdiff::fracdiff.sim(10000, d = 0.2), times = 33)"

RObject{VecSxp}
Unit: milliseconds
                                   expr      min       lq     mean   median
 fracdiff::fracdiff.sim(10000, d = 0.2) 101.2691 106.6494 112.2443 110.4792
       uq      max neval
 114.2689 164.3293    33

Note that the times are similar. Hence, for ease of use, the next
benchmarks are done using ***BenchmarkTools***.

# Fractional differencing

## The *fi_gen()* function

In [6]:
@benchmark fracdiff(randn(10000,1), 0.2)

BenchmarkTools.Trial: 6432 samples with 1 evaluation.
 Range ( min … max ): 564.900 μs … 23.529 ms ┊ GC ( min … max ): 0.00% … 3.52%
 Time ( median ): 639.400 μs ┊ GC ( median ): 0.00%
 Time ( mean ± σ ): 770.664 μs ± 515.671 μs ┊ GC ( mean ± σ ): 4.99% ± 9.82%
 ▂▇█ ▇ ▅▄▃▃▂ ▂ ▁▁▁▁ ▁▁ ▁ ▁▂▂▂▂▁▁ ▂
 ███ █ █████ █ ███████████████▇▇████████████▇▇▇▅▆▆▅▅▅▄▁▅▅▆▅▃▅▅▅▅▅▅ █
 565 μs Histogram: log( frequency ) by time 2.01 ms < 
 Memory estimate : 2.58 MiB , allocs estimate : 44 .

## R: *fracdiff::diffseries()*

The ***R*** package **fracdiff** is used for fractional differencing
using ***fracdiff::diffseries()***.

In [7]:
@benchmark R"fracdiff::diffseries(rnorm(10000), d = 0.2)"

BenchmarkTools.Trial: 1905 samples with 1 evaluation.
 Range ( min … max ): 1.829 ms … 39.174 ms ┊ GC ( min … max ): 0.00% … 0.00%
 Time ( median ): 2.205 ms ┊ GC ( median ): 0.00%
 Time ( mean ± σ ): 2.611 ms ± 1.661 ms ┊ GC ( mean ± σ ): 0.00% ± 0.00%
 ▃█▇▃ 
 ▄████ ▇ ▆▆▆▆ ▄ ▄▄▄▄▃▃▃▃▃▂▂▂▂▃▂▂▂▂▂▂▁▂▃▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▁▂▂▂▂▂▂▂▂ ▃
 1.83 ms Histogram: frequency by time 6.32 ms < 
 Memory estimate : 1.02 KiB , allocs estimate : 37 .

## R: *LongMemoryTS:fdiff()*

Loading the ***R*** package **LongMemoryTS**. The
***LongMemoryTS::fdiff()*** function is used for fractional
differencing.

In [8]:
R"library(LongMemoryTS)"
@benchmark R"LongMemoryTS::fdiff(rnorm(10000), 0.2)"

BenchmarkTools.Trial: 1079 samples with 1 evaluation.
 Range ( min … max ): 3.590 ms … 48.788 ms ┊ GC ( min … max ): 0.00% … 0.00%
 Time ( median ): 4.247 ms ┊ GC ( median ): 0.00%
 Time ( mean ± σ ): 4.615 ms ± 1.969 ms ┊ GC ( mean ± σ ): 0.00% ± 0.00%
 ▃▅▆█▆▇▃ ▄ ▄▄▂ 
 ▇███████ █ ███▇ ▇ ▇▆▄▅▄▄▃▄▃▃▃▃▃▄▂▄▃▄▂▃▃▃▃▃▃▃▃▂▃▂▂▁▂▂▂▃▂▁▂▁▂▂▂▂ ▄
 3.59 ms Histogram: frequency by time 8.17 ms < 
 Memory estimate : 1.02 KiB , allocs estimate : 37 .

## Comparing accuracy

In [9]:
t = 20
x = randn(t,1)
d = 0.2

fd_LongMemoryjl = fracdiff(x, d)
fd_fracdiff = R"fracdiff::diffseries($x, d = $d)"[1:t]
fd_LongMemoryTS = R"LongMemoryTS::fdiff($x, d = $d)"[1:t]

[fd_LongMemoryjl fd_fracdiff fd_LongMemoryTS]

20×3 Matrix{Float64}:
 -0.414687   -0.037776    -0.414687
 -1.3211     -1.01957     -1.3211
  1.19154     1.46292      1.19154
  0.127951    0.381236     0.127951
 -1.16742    -0.926802    -1.16742
 -0.819538   -0.588542    -0.819538
  1.07604     1.29934      1.07604
  0.13666     0.353575     0.13666
 -0.153646    0.0578465   -0.153646
 -2.65003    -2.44324     -2.65003
  1.70449     1.90714      1.70449
  0.228423    0.427395     0.228423
 -2.45395    -2.25829     -2.45395
 -0.527068   -0.334422    -0.527068
  0.475296    0.66519      0.475296
 -0.180992    0.00637046  -0.180992
  0.0605239   0.245544     0.0605239
  0.963221    1.14606      0.963221
 -1.19026    -1.00945     -1.19026
  0.877683    1.05659      0.877683

# Long memory estimation

Data generation.

In [10]:
x = fi_gen(1000, 0.4);

## The *gph_est()* function

In [11]:
@benchmark gph_est(x; m = 0.5)

BenchmarkTools.Trial: 10000 samples with 1 evaluation.
 Range ( min … max ): 36.800 μs … 5.649 ms ┊ GC ( min … max ): 0.00% … 40.07%
 Time ( median ): 48.800 μs ┊ GC ( median ): 0.00%
 Time ( mean ± σ ): 64.392 μs ± 141.659 μs ┊ GC ( mean ± σ ): 3.70% ± 1.74%
 ▃█▄▁ 
 ▄████ █ ▆▅▅▄▄▄ ▃ ▃▃▃▃▄▃▃▃▃▃▃▃▃▃▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▂▁▂▂▂▂ ▃
 36.8 μs Histogram: frequency by time 181 μs < 
 Memory estimate : 66.48 KiB , allocs estimate : 43 .

## LongMemoryTS: *gph()*

In [12]:
@benchmark R"LongMemoryTS::gph($x, m = floor(1000^0.5))"

BenchmarkTools.Trial: 10000 samples with 1 evaluation.
 Range ( min … max ): 163.300 μs … 9.850 ms ┊ GC ( min … max ): 0.00% … 0.00%
 Time ( median ): 192.100 μs ┊ GC ( median ): 0.00%
 Time ( mean ± σ ): 231.772 μs ± 198.988 μs ┊ GC ( mean ± σ ): 0.00% ± 0.00%
 ▅█▅ ▁ 
 ▁▃████ █ ▆▄▃▃▃▂▂▂ ▂ ▂▂▂▂▂▂▂▂▂▂▂▂▁▂▁▁▂▂▂▃▃▃▂▂▂▂▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁ ▂
 163 μs Histogram: frequency by time 441 μs < 
 Memory estimate : 2.66 KiB , allocs estimate : 104 .

## fracdiff: *fdGPH()*

In [13]:
@benchmark R"fracdiff::fdGPH($x)"

BenchmarkTools.Trial: 663 samples with 1 evaluation.
 Range ( min … max ): 5.115 ms … 35.875 ms ┊ GC ( min … max ): 0.00% … 0.00%
 Time ( median ): 6.391 ms ┊ GC ( median ): 0.00%
 Time ( mean ± σ ): 7.530 ms ± 3.526 ms ┊ GC ( mean ± σ ): 0.00% ± 0.00%
 ▆█ ▁ 
 ▆██ █ ▆ ▄ ▃▂▃▄▅▄▃▃▃▂▂▂▂▂▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▁▂▁▁▁▁▁▁▁▁▁▁▁▁▁▂ ▃
 5.12 ms Histogram: frequency by time 32 ms < 
 Memory estimate : 2.66 KiB , allocs estimate : 104 .

## Comparing accuracy

In [14]:
gph_LongMemoryjl = gph_est(x; m = 0.5)
gph_LongMemoryTS = R"LongMemoryTS::gph(X = $x, m = floor(1000^0.5))"[1]
gph_fracdiff = R"fracdiff::fdGPH($x)$d"[1]

[gph_LongMemoryjl gph_LongMemoryTS gph_fracdiff]

1×3 Matrix{Float64}:
 0.273802  0.273945  0.273945